In [1]:
import pandas as pd
import numpy as np 
import matplotlib.pyplot as plt
import seaborn as sns
#import preprocessor as p
import re
import warnings
warnings.filterwarnings("ignore")
from bs4 import BeautifulSoup
import string
import html
import requests
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn import metrics
from sklearn.linear_model import LogisticRegression
from sklearn.svm import LinearSVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import MultinomialNB
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
import nltk
from nltk import word_tokenize, FreqDist
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.tokenize import word_tokenize, RegexpTokenizer
from nltk.corpus import stopwords
nltk.download
nltk.download('wordnet')
nltk.download('stopwords')
nltk.download('vader_lexicon')
nltk.download('punkt')
from nltk.tokenize import TweetTokenizer
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC
import os
import pickle
from sklearn.metrics import classification_report, accuracy_score
from google.colab import files
import io

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [2]:
!pip install preprocessor
!pip install bertopic

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for preprocessor: filename=preprocessor-1.1.3-py3-none-any.whl size=4473 sha256=ba6dc1e78e4a4ab13ab269a2d139d09f6b0b106230950044ae2eeb56f242a55f
  Stored in directory: /root/.cache/pip/wheels/18/41/3e/30e0c08b0759166f31aee174d58d288ad5c277bd102c8ad869
Successfully built preprocessor
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 120.7/120.7 KB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.2/88.2 KB 13.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 65.5 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [3]:
uploaded = files.upload()
df_russiawar_may = pd.read_csv(io.BytesIO(uploaded['tweet_russiawar_may.csv']))

Saving tweet_russiawar_may.csv to tweet_russiawar_may.csv


In [4]:
uploaded = files.upload()
df_russiawar_jun = pd.read_csv(io.BytesIO(uploaded['tweet_russiawar_jun.csv']))

Saving tweet_russiawar_jun.csv to tweet_russiawar_jun.csv


In [5]:
uploaded = files.upload()
df_russiawar_jul = pd.read_csv(io.BytesIO(uploaded['tweet_russiawar_jul.csv']))

Saving tweet_russiawar_jul.csv to tweet_russiawar_jul.csv


In [5]:
df_russiawar_may = pd.read_csv('tweet_russiawar_may.csv')
df_russiawar_jun = pd.read_csv('tweet_russiawar_jun.csv')
df_russiawar_jul = pd.read_csv('tweet_russiawar_jul.csv')

In [6]:
col = ["Unnamed:0", "ID", "Date", "Tweet"]
df_russiawar = pd.DataFrame(columns=col)

df_russiawar = pd.concat([df_russiawar, df_russiawar_may])
df_russiawar = pd.concat([df_russiawar, df_russiawar_jun])
df_russiawar = pd.concat([df_russiawar, df_russiawar_jul])

In [7]:
def clean_text(_sentence):

    #removes emojis, pictographs, map symbols and flags
    emoji_pattern = re.compile(pattern = "["
          u"\U0001F600-\U0001F64F" 
          u"\U0001F300-\U0001F5FF" 
          u"\U0001F680-\U0001F6FF" 
          u"\U0001F1E0-\U0001F1FF" 
                            "]+", flags = re.UNICODE)
    _sentence = emoji_pattern.sub(r'',_sentence)

    #emoves tags and attributes
    _sentence = re.sub('(<[^>]*>)','',_sentence)

    #converts character code to string
    _sentence = html.unescape(_sentence)

    #removes urls
    _sentence = re.sub("(\w+:\/\/\S+)|(http[^\s]+)|(www.[^\s]+)",'',_sentence, flags=re.MULTILINE)
    
    #removes RT
    _sentence = re.sub("RT",'',_sentence)
    
    #converts the sentence to a lower case
    _sentence = _sentence.lower()

    #removes punctuation
    _sentence = re.sub(r'\@\w+|\#\w+','', _sentence)
    _sentence = _sentence.translate(str.maketrans('', '', (string.punctuation)))
    
    #checks for stop words
    stop_words = set(stopwords.words('english'))
    _sentence = [word for word in str(_sentence).split() if word not in stop_words]

    #joins the word and returns a sentence
    return " ".join(_sentence)

#function to preprocess tweets
def preprocess_tweets(tweets_df,column):

    #apply clean text in a vectorized format
    vfunc_clean_text = np.vectorize(clean_text)
    tweets_df[column] = vfunc_clean_text(tweets_df[column]) #create a new column that consists of preprocessed tweets
    
    return tweets_df

In [8]:
data_df_russiawar = preprocess_tweets(df_russiawar,'Tweet')

In [9]:
def Vader_process(data_df):
    sid = SentimentIntensityAnalyzer()
    res = [*data_df['Tweet'].apply(sid.polarity_scores)]
    #print(res[:3])

    sentiment_df = pd.DataFrame.from_records(res)
    data_df = pd.concat([data_df.reset_index(drop=True), sentiment_df.reset_index(drop=True)], axis=1, join="inner")
    #print(data_df.head())
    
    conditions = [
    (data_df['compound'] <= -0.5),
    (data_df['compound'] > -0.5) & (data_df['compound'] < 0.5),
    (data_df['compound'] >= 0.5)
    ]

    values = [0, -1, 1]
    data_df['label'] = np.select(conditions, values)

    #print(data_df.head())
    
    X_df = data_df[data_df.label != -1]
    X_df = X_df[['Tweet','label']]
    #print(X_df.head())
    
    return X_df

In [10]:
X_russiawar = Vader_process(data_df_russiawar)

In [11]:
X_russiawar

Tweet  label
1       ukrainian people shall defend ukraines indepen...      0
2                                   ukraine vs russia war      0
4       erdoğan talked un secretary general phone disc...      0
5       especially since everyone politely ignored got...      0
6       survey conducted ukrainerussia war devastating...      0
...                                                   ...    ...
505992  ukrainerussia war kamikaze drone flew room rus...      0
505993  im outside irish political context find idea u...      0
505994  war w russia war china war w middle east techn...      0
505995  possible dems hoping russia war would bail ele...      0
505998  facts one twitter check economic indices 2015 ...      0

[364360 rows x 2 columns]

In [12]:
X_russiawar.to_csv("X_russiawar.csv")

**BERTopic Modelling**

In [13]:
import nltk
from nltk.corpus import stopwords
from umap import UMAP
from bertopic import BERTopic

In [14]:
umap_model = UMAP(random_state=3231)
bert_topic_model= BERTopic(embedding_model = "all-MiniLM-L6-v2", umap_model=umap_model)

bert_negative = X_russiawar[X_russiawar['label']==0] #change this to 1 if positive. keep 0 if negative.
bert_negative = bert_negative.Tweet.tolist()
topics, probs = bert_topic_model.fit_transform(bert_negative)

In [15]:
pd.set_option('display.max_rows', None)


In [16]:
topic_list=bert_topic_model.get_topic_info()
topic_list

Topic  Count                                               Name
0         -1   2685              -1_youtuber_disruptive_links_favoreat
1          0    981                     0_col_douglas_macgregor_update
2          1    810                         1_updates_latest_news_live
3          2    728                2_debunks_colonel_douglas_macgregor
4          3    671                          3_ritter_scott_update_via
5          4    658                           4_york_times_updates_new
6          5    656                  5_coverage_live_ukrainerussia_war
7          6    650                             6_as_drivers_takes_pay
8          7    635                               7_oust_coup_ready_he
9          8    624                     8_moscows_costly_shows_failure
10         9    589                               9_links_russias_war_
11        10    568                             10_ukraine_russia_war_
12        11    566                     11_15th_package_bringing_total
13        12    552                          12_york_times_updates_new
14        13    534            13_newsworldpress_15th_package_bringing
15        14    520                14_lecturer_accuse_sharing_students
16        15    507               15_debunks_colonel_douglas_macgregor
17        16    493             16_loophole_uncover_punishment_extreme
18        17    482                          17_york_times_updates_new
19        18    470                     18_advance_flee_frontline_city
20        19    467                  19_exbritish_backed_spy_seriously
21        20    466                   20_vanish_payback_declaring_seek
22        21    464                  21_passes_outnumbered_mobilise_1m
23        22    459                   22_resurface_graft_concerns_goes
24        23    458                           23_york_times_new_latest
25        24    456                          24_dims_outlook_bank_amid
26        25    454           25_puffyfaced_displays_signals_deadliest
27        26    451                  26_tended_dead_soldiers_ukrainian
28        27    447             27_rebel_backlash_immediate_withdrawal
29        28    443                    28_maniac_shameful_turns_puppet
30        29    439                    29_col_douglas_macgregor_update
31        30    427                30_reactions_belong_italian_origins
32        31    419                  31_spotted_storming_squads_wagner
33        32    414                     32_delivering_delay_edge_gives
34        33    413                     33_advance_flee_frontline_city
35        34    412          34_terminator_unleashes_battered_vehicles
36        35    409                   35_resurface_graft_concerns_goes
37        36    403                     36_15th_package_bringing_total
38        37    397                       37_blasts_mykolaiv_rock_news
39        38    394                     38_advance_flee_frontline_city
40        39    390                 39_reaches_outnumbered_mobilise_1m
41        40    382                     40_15th_package_bringing_total
42        41    380           41_assassins_minutes_family_bloodthirsty
43        42    367                        42_updates_latest_news_live
44        43    365             43_miscalculations_appalling_no_choice
45        44    365                        44_updates_latest_news_live
46        45    358                      45_blink_grip_madman_paranoid
47        46    358               46_twitches_hunched_fidgets_fuelling
48        47    337                   47_torchering_ladies_sheilds_ugh
49        48    333                      48_mutiny_accused_sending_die
50        49    322                        49_mom_jill_hard_understand
51        50    316                  50_strict_weekend_planned_warning
52        51    310                       51_feared_escalates_60_ahead
53        52    304             52_agony_violates_steelworks_ceasefire
54        53    301               53_shattering_governments_youre_fall
55        54    291            

In [17]:
bert_topic_model.visualize_barchart()

In [18]:
#Positive
umap_model = UMAP(random_state=3231)
bert_topic_model= BERTopic(embedding_model = "all-MiniLM-L6-v2", umap_model=umap_model)

bert_positive = X_russiawar[X_russiawar['label']==1] #change this to 1 if positive. keep 0 if negative.
bert_positive = bert_positive.Tweet.tolist()
topics, probs = bert_topic_model.fit_transform(bert_positive)

pd.set_option('display.max_rows', None)
topic_list=bert_topic_model.get_topic_info()
topic_list

bert_topic_model.visualize_barchart()